In [1]:
import numpy as np
import pandas as pd
import keras
import warnings
warnings.filterwarnings(action='ignore')
import sys

from keras.models import Sequential
from keras.layers import Dense,Dropout

### Data 불러오기

In [2]:
data = pd.read_csv('data_preprocessing.csv')
data

year  month CARD_SIDO_NM CARD_CCG_NM STD_CLSS_NM  SEX  region_diff  \
0        2019      1           강원         강릉시  건강보조식품 소매업    1            1   
1        2019      1           강원         강릉시  건강보조식품 소매업    1            1   
2        2019      1           강원         강릉시  건강보조식품 소매업    1            1   
3        2019      1           강원         강릉시  건강보조식품 소매업    1            1   
4        2019      1           강원         강릉시  건강보조식품 소매업    1            1   
...       ...    ...          ...         ...         ...  ...          ...   
2691680  2020      3           충북         충주시    휴양콘도 운영업    1            1   
2691681  2020      3           충북         충주시    휴양콘도 운영업    1            1   
2691682  2020      3           충북         충주시    휴양콘도 운영업    1            1   
2691683  2020      3           충북         충주시    휴양콘도 운영업    1            1   
2691684  2020      3           충북         충주시    휴양콘도 운영업    2            1   

         AGE  CSTMR_CNT  CNT      AMT  
0         20          4    4   311200  
1         30          7    8  1374500  
2         40          7    8  2764300  
3         50         21   21  3690830  
4         60         19   20  1433500  
...      ...        ...  ...      ...  
2691680   30          3    4    43300  
2691681   40          3    3    35000  
2691682   50          4    6   188000  
2691683   60          3    3   194000  
2691684   50          4    6    99000  

[2691685 rows x 11 columns]

### SET Pred_Dataframe

In [3]:
def Pred_data_def(raw_data):
    temp         = []
    SEX          = raw_data['SEX'].unique()
    Region_diff  = raw_data['region_diff'].unique()
    AGE          = raw_data['AGE'].unique()
    month        = [4,7]
    CARD_SIDO_NM = raw_data['CARD_SIDO_NM'].unique()
    STD_CLSS_NM  = raw_data['STD_CLSS_NM'].unique()
    
    for sido in CARD_SIDO_NM:
        df = raw_data[raw_data["CARD_SIDO_NM"] == sido]
        ccg_list = df['CARD_CCG_NM'].unique()
        for ccg in ccg_list:
            for std in STD_CLSS_NM:
                for age in AGE: 
                    for sex in SEX:
                        for region in Region_diff:
                            for i in month:
                                temp.append([i, sido, ccg, std, sex, region, age])

    temp = np.array(temp)
    Pred_data = pd.DataFrame(data= temp, columns= ['month', 'CARD_SIDO_NM', 'CARD_CCG_NM',
                                                   'STD_CLSS_NM', 'SEX', 'region_diff', 'AGE'])
    return Pred_data

### Train, Pred 구분

In [4]:
Train_data = data.loc[(data['year']==2020)&((data['month']==1)|(data['month']==2)|
                                              (data['month']==3))]
Train_data_X = Train_data.drop(['AMT','year','CNT','CSTMR_CNT'],axis=1)
Train_data = Train_data.drop(['CNT','year','CSTMR_CNT'],axis=1)
Pred_data = Pred_data_def(Train_data_X)

print('Pred_data :',Pred_data.shape,
     '\nTrain_data :',Train_data.shape,
     '\nTrain_data_X :',Train_data_X.shape)

Pred_data : (861000, 7) 
Train_data : (521750, 8) 
Train_data_X : (521750, 7)


### Encoding

In [5]:
dum_col     = ['CARD_CCG_NM','SEX','region_diff','AGE']
Train_data_en = pd.get_dummies(Train_data, columns=dum_col)
Pred_data_en  = pd.get_dummies(Pred_data, columns=dum_col)

### Model

In [6]:
### 세팅중
# pred_data   = Pred_data.copy()
# pred_data.drop(['SEX','region_diff','AGE','CARD_SIDO_NM','STD_CLSS_NM'],axis=1, inplace=True)
final_data  = []
sido_list   = Train_data_en['CARD_SIDO_NM'].unique()[8:9]
std_list    = Train_data_en['STD_CLSS_NM'].unique()

for i, sido in enumerate(sido_list):
    for j, std in enumerate(std_list):      
        
        df_train1 = Train_data_en[(Train_data_en['CARD_SIDO_NM'] == sido) & (Train_data_en['STD_CLSS_NM'] == std)]                
        df_pred   = Pred_data_en[(Pred_data_en['CARD_SIDO_NM'] == sido) & (Pred_data_en['STD_CLSS_NM'] == std)]
        print("★ ", i, j)
        
        #DF가 비어있을때 학습X
        if( df_train1.empty): 
            print("train가 비어있음")
            continue

        y_train = df_train1['AMT'].to_numpy(dtype=np.float32).reshape(-1,1)
        X_train = df_train1.drop(['AMT','CARD_SIDO_NM','STD_CLSS_NM'],axis=1).to_numpy(dtype=np.float32)
        X_test = df_pred.drop(['CARD_SIDO_NM','STD_CLSS_NM'],axis=1).to_numpy(dtype=np.float32)        

        print("sido: {}번째 / std: {}번째".format(sido, std))
        print('TRAIN : ',X_train.shape,y_train.shape,
             '\nTEST : ',X_test.shape)

        print('-'*30)

        num_hidden_units = 150
        input_dim = X_train.shape[1]

        model = Sequential()
        model.add(Dense(num_hidden_units,input_dim = input_dim, activation='relu'))
        model.add(Dropout(0.2))
        model.add(Dense(num_hidden_units,kernel_initializer='normal', activation='relu'))
        model.add(Dropout(0.2))
        model.add(Dense(num_hidden_units,kernel_initializer='normal', activation='relu'))
        model.add(Dropout(0.2))
        model.add(Dense(num_hidden_units,kernel_initializer='normal', activation='relu'))
        model.add(Dropout(0.2))
        model.add(Dense(num_hidden_units, kernel_initializer='normal',activation='relu'))
        model.add(Dropout(0.2))
        model.add(Dense(num_hidden_units,kernel_initializer='normal', activation='relu'))
        model.add(Dense(num_hidden_units,kernel_initializer='normal', activation='relu'))
        model.add(Dense(1))
        model.compile(loss='MeanAbsolutePercentageError', optimizer='adam', metrics=['accuracy'])
        model.fit(X_train, y_train, epochs=1000, batch_size=3, verbose=1)
        
        # 예측
        pred = model.predict(X_test)
        df_pred['AMT'] = np.round(pred, 0)
        df_pred['REG_YYMM'] = ('20200' + df_pred['month']).astype('int64')
        df_pred['CARD_SIDO_NM'] = sido
        df_pred['STD_CLSS_NM']  = std
        df_pred = df_pred[['REG_YYMM', 'CARD_SIDO_NM', 'STD_CLSS_NM', 'AMT']]
        df_pred = df_pred.groupby(['REG_YYMM', 'CARD_SIDO_NM', 'STD_CLSS_NM']).sum().reset_index(drop=False) 
        fin = pd.DataFrame(df_pred[0:1])
        final_data.append(fin.values)
        fin = pd.DataFrame(df_pred[1:2])
        final_data.append(fin.values)

★  0 0
sido: 서울번째 / std: 건강보조식품 소매업번째
TRAIN :  (1552, 240) (1552, 1) 
TEST :  (2100, 240)
------------------------------
Epoch 1/1000
518/518 [==============================] - 1s 2ms/step - loss: 90.9282 - accuracy: 0.0000e+00
Epoch 2/1000
518/518 [==============================] - 1s 2ms/step - loss: 86.1802 - accuracy: 0.0000e+00
Epoch 3/1000
518/518 [==============================] - 1s 2ms/step - loss: 82.2991 - accuracy: 0.0000e+00
Epoch 4/1000
518/518 [==============================] - 1s 2ms/step - loss: 79.8303 - accuracy: 0.0000e+00
Epoch 5/1000
518/518 [==============================] - 1s 2ms/step - loss: 78.1316 - accuracy: 0.0000e+00
Epoch 6/1000
518/518 [==============================] - 1s 2ms/step - loss: 75.0410 - accuracy: 0.0000e+00
Epoch 7/1000
518/518 [==============================] - 1s 2ms/step - loss: 74.0442 - accuracy: 0.0000e+00
Epoch 8/1000
518/518 [==============================] - 1s 2ms/step - loss: 72.4239 - accuracy: 0.0000e+00
Epoch 9/1000
518/518 [=

518/518 [==============================] - 1s 1ms/step - loss: 36.7364 - accuracy: 0.0000e+00
Epoch 76/1000
518/518 [==============================] - 1s 1ms/step - loss: 37.8586 - accuracy: 0.0000e+00
Epoch 77/1000
518/518 [==============================] - 1s 1ms/step - loss: 37.3776 - accuracy: 0.0000e+00
Epoch 78/1000
518/518 [==============================] - 1s 1ms/step - loss: 37.4648 - accuracy: 0.0000e+00
Epoch 79/1000
518/518 [==============================] - 1s 1ms/step - loss: 37.6716 - accuracy: 0.0000e+00
Epoch 80/1000
518/518 [==============================] - 1s 1ms/step - loss: 37.0963 - accuracy: 0.0000e+00
Epoch 81/1000
518/518 [==============================] - 1s 2ms/step - loss: 36.8760 - accuracy: 0.0000e+00
Epoch 82/1000
518/518 [==============================] - 1s 1ms/step - loss: 37.0050 - accuracy: 0.0000e+00
Epoch 83/1000
518/518 [==============================] - 1s 1ms/step - loss: 36.7910 - accuracy: 0.0000e+00
Epoch 84/1000
518/518 [===================

518/518 [==============================] - 1s 2ms/step - loss: 32.0106 - accuracy: 0.0000e+00
Epoch 151/1000
518/518 [==============================] - 1s 2ms/step - loss: 31.5080 - accuracy: 0.0000e+00
Epoch 152/1000
518/518 [==============================] - 1s 2ms/step - loss: 31.6458 - accuracy: 0.0000e+00
Epoch 153/1000
518/518 [==============================] - 1s 2ms/step - loss: 31.3122 - accuracy: 0.0000e+00
Epoch 154/1000
518/518 [==============================] - 1s 2ms/step - loss: 31.9428 - accuracy: 0.0000e+00
Epoch 155/1000
518/518 [==============================] - 1s 2ms/step - loss: 31.5894 - accuracy: 0.0000e+00
Epoch 156/1000
518/518 [==============================] - 1s 2ms/step - loss: 30.7483 - accuracy: 0.0000e+00
Epoch 157/1000
518/518 [==============================] - 1s 2ms/step - loss: 30.9563 - accuracy: 0.0000e+00
Epoch 158/1000
518/518 [==============================] - 1s 2ms/step - loss: 31.9599 - accuracy: 0.0000e+00
Epoch 159/1000
518/518 [==========

518/518 [==============================] - 1s 1ms/step - loss: 29.2885 - accuracy: 0.0000e+00A: 0s - loss: 28.2315 - accuracy:
Epoch 225/1000
518/518 [==============================] - 1s 1ms/step - loss: 29.1616 - accuracy: 0.0000e+00
Epoch 226/1000
518/518 [==============================] - 1s 1ms/step - loss: 28.7232 - accuracy: 0.0000e+00
Epoch 227/1000
518/518 [==============================] - 1s 1ms/step - loss: 29.2514 - accuracy: 0.0000e+00
Epoch 228/1000
518/518 [==============================] - 1s 1ms/step - loss: 28.1357 - accuracy: 0.0000e+00
Epoch 229/1000
518/518 [==============================] - 1s 1ms/step - loss: 28.1338 - accuracy: 0.0000e+00
Epoch 230/1000
518/518 [==============================] - 1s 1ms/step - loss: 29.2184 - accuracy: 0.0000e+00
Epoch 231/1000
518/518 [==============================] - 1s 1ms/step - loss: 28.1490 - accuracy: 0.0000e+00
Epoch 232/1000
518/518 [==============================] - 1s 1ms/step - loss: 28.4333 - accuracy: 0.0000e+00
E

Epoch 299/1000
518/518 [==============================] - 1s 1ms/step - loss: 27.2111 - accuracy: 0.0000e+00
Epoch 300/1000
518/518 [==============================] - 1s 1ms/step - loss: 26.2470 - accuracy: 0.0000e+00
Epoch 301/1000
518/518 [==============================] - 1s 1ms/step - loss: 26.0763 - accuracy: 0.0000e+00
Epoch 302/1000
518/518 [==============================] - 1s 1ms/step - loss: 26.6865 - accuracy: 0.0000e+00
Epoch 303/1000
518/518 [==============================] - 1s 1ms/step - loss: 26.5161 - accuracy: 0.0000e+00
Epoch 304/1000
518/518 [==============================] - 1s 1ms/step - loss: 25.6871 - accuracy: 0.0000e+00
Epoch 305/1000
518/518 [==============================] - 1s 1ms/step - loss: 26.8827 - accuracy: 0.0000e+00
Epoch 306/1000
518/518 [==============================] - 1s 1ms/step - loss: 26.6707 - accuracy: 0.0000e+00
Epoch 307/1000
518/518 [==============================] - 1s 1ms/step - loss: 26.6529 - accuracy: 0.0000e+00
Epoch 308/1000
518/

...

66/66 [==============================] - 0s 1ms/step - loss: 19.0342 - accuracy: 0.0000e+00
Epoch 693/1000
66/66 [==============================] - 0s 1ms/step - loss: 15.9207 - accuracy: 0.0000e+00
Epoch 694/1000
66/66 [==============================] - 0s 1ms/step - loss: 20.1185 - accuracy: 0.0000e+00
Epoch 695/1000
66/66 [==============================] - 0s 1ms/step - loss: 17.6503 - accuracy: 0.0000e+00
Epoch 696/1000
66/66 [==============================] - 0s 1ms/step - loss: 18.8116 - accuracy: 0.0000e+00
Epoch 697/1000
66/66 [==============================] - 0s 1ms/step - loss: 16.9305 - accuracy: 0.0000e+00A: 0s - loss: 15.2360 - accuracy: 0.0000e+0
Epoch 698/1000
66/66 [==============================] - 0s 1ms/step - loss: 18.1302 - accuracy: 0.0000e+00
Epoch 699/1000
66/66 [==============================] - 0s 1ms/step - loss: 19.0750 - accuracy: 0.0000e+00
Epoch 700/1000
66/66 [==============================] - 0s 1ms/step - loss: 18.5290 - accuracy: 0.0000e+00
Epoch 701

66/66 [==============================] - 0s 1ms/step - loss: 18.4403 - accuracy: 0.0000e+00
Epoch 769/1000
66/66 [==============================] - 0s 1ms/step - loss: 17.5750 - accuracy: 0.0000e+00
Epoch 770/1000
66/66 [==============================] - 0s 1ms/step - loss: 18.3155 - accuracy: 0.0000e+00
Epoch 771/1000
66/66 [==============================] - 0s 1ms/step - loss: 18.5472 - accuracy: 0.0000e+00
Epoch 772/1000
66/66 [==============================] - 0s 1ms/step - loss: 17.8371 - accuracy: 0.0000e+00
Epoch 773/1000
66/66 [==============================] - 0s 1ms/step - loss: 16.3761 - accuracy: 0.0000e+00
Epoch 774/1000
66/66 [==============================] - 0s 1ms/step - loss: 16.8180 - accuracy: 0.0000e+00
Epoch 775/1000
66/66 [==============================] - 0s 1ms/step - loss: 17.5154 - accuracy: 0.0000e+00
Epoch 776/1000
66/66 [==============================] - 0s 1ms/step - loss: 19.6983 - accuracy: 0.0000e+00
Epoch 777/1000
66/66 [==============================

66/66 [==============================] - 0s 1ms/step - loss: 18.4563 - accuracy: 0.0000e+00
Epoch 845/1000
66/66 [==============================] - 0s 1ms/step - loss: 18.6571 - accuracy: 0.0000e+00
Epoch 846/1000
66/66 [==============================] - 0s 1ms/step - loss: 16.4941 - accuracy: 0.0000e+00
Epoch 847/1000
66/66 [==============================] - 0s 1ms/step - loss: 16.5759 - accuracy: 0.0000e+00
Epoch 848/1000
66/66 [==============================] - 0s 1ms/step - loss: 19.7139 - accuracy: 0.0000e+00
Epoch 849/1000
66/66 [==============================] - 0s 1ms/step - loss: 18.2272 - accuracy: 0.0000e+00
Epoch 850/1000
66/66 [==============================] - 0s 1ms/step - loss: 15.6629 - accuracy: 0.0000e+00
Epoch 851/1000
66/66 [==============================] - 0s 1ms/step - loss: 16.9308 - accuracy: 0.0000e+00
Epoch 852/1000
66/66 [==============================] - 0s 1ms/step - loss: 17.7186 - accuracy: 0.0000e+00
Epoch 853/1000
66/66 [==============================

66/66 [==============================] - 0s 1ms/step - loss: 17.4098 - accuracy: 0.0000e+00
Epoch 921/1000
66/66 [==============================] - 0s 1ms/step - loss: 16.9692 - accuracy: 0.0000e+00
Epoch 922/1000
66/66 [==============================] - 0s 1ms/step - loss: 19.6155 - accuracy: 0.0000e+00
Epoch 923/1000
66/66 [==============================] - 0s 1ms/step - loss: 17.4608 - accuracy: 0.0000e+00
Epoch 924/1000
66/66 [==============================] - 0s 1ms/step - loss: 17.9689 - accuracy: 0.0000e+00
Epoch 925/1000
66/66 [==============================] - 0s 1ms/step - loss: 16.3917 - accuracy: 0.0000e+00
Epoch 926/1000
66/66 [==============================] - 0s 1ms/step - loss: 15.9319 - accuracy: 0.0000e+00
Epoch 927/1000
66/66 [==============================] - 0s 1ms/step - loss: 16.8924 - accuracy: 0.0000e+00
Epoch 928/1000
66/66 [==============================] - 0s 1ms/step - loss: 17.1100 - accuracy: 0.0000e+00
Epoch 929/1000
66/66 [==============================

66/66 [==============================] - 0s 1ms/step - loss: 16.1502 - accuracy: 0.0000e+00
Epoch 997/1000
66/66 [==============================] - 0s 1ms/step - loss: 16.4478 - accuracy: 0.0000e+00
Epoch 998/1000
66/66 [==============================] - 0s 1ms/step - loss: 17.0717 - accuracy: 0.0000e+00
Epoch 999/1000
66/66 [==============================] - 0s 1ms/step - loss: 15.1955 - accuracy: 0.0000e+00
Epoch 1000/1000
66/66 [==============================] - 0s 1ms/step - loss: 17.8371 - accuracy: 0.0000e+00


### Pred_DF with AMT

In [7]:
col = ['REG_YYMM', 'CARD_SIDO_NM', 'STD_CLSS_NM', 'AMT']
Final_data = pd.DataFrame(columns=col)
for data in range(len(final_data)):
    frist_df = pd.DataFrame(final_data[data],columns=col)
    Final_data = Final_data.append(frist_df)
Final_data

REG_YYMM CARD_SIDO_NM  STD_CLSS_NM          AMT
0    202004           서울   건강보조식품 소매업  1.69013e+09
0    202007           서울   건강보조식품 소매업  4.40478e+09
0    202004           서울      골프장 운영업  6.94458e+09
0    202007           서울      골프장 운영업  2.71121e+10
0    202004           서울  과실 및 채소 소매업  9.43015e+09
..      ...          ...          ...          ...
0    202007           서울       택시 운송업  5.91872e+10
0    202004           서울    내항 여객 운송업  7.06958e+09
0    202007           서울    내항 여객 운송업  1.29287e+10
0    202004           서울    정기 항공 운송업  2.75269e+09
0    202007           서울    정기 항공 운송업  3.42041e+09

[78 rows x 4 columns]

### Save to csv

In [8]:
submission = pd.read_csv('submission_mingsu.csv',index_col = 0)
submission = submission.drop(['AMT'], axis=1)
submission = submission.merge(Final_data, left_on=['REG_YYMM', 'CARD_SIDO_NM', 'STD_CLSS_NM'], right_on=['REG_YYMM', 'CARD_SIDO_NM', 'STD_CLSS_NM'], how='left')
submission.index.name = 'id'
submission.to_csv('submission_mingsu(8번째).csv', encoding='utf-8-sig')
submission.head(10)

REG_YYMM CARD_SIDO_NM           STD_CLSS_NM  AMT
id                                                 
0    202004           강원            건강보조식품 소매업  NaN
1    202004           강원               골프장 운영업  NaN
2    202004           강원           과실 및 채소 소매업  NaN
3    202004           강원     관광 민예품 및 선물용품 소매업  NaN
4    202004           강원  그외 기타 분류안된 오락관련 서비스업  NaN
5    202004           강원       그외 기타 스포츠시설 운영업  NaN
6    202004           강원          그외 기타 종합 소매업  NaN
7    202004           강원          기타 대형 종합 소매업  NaN
8    202004           강원          기타 수상오락 서비스업  NaN
9    202004           강원           기타 외국식 음식점업  NaN